<h1>Extra credit for MTH 335</h1>

<p>This is worth 5 points extra credit on test scores.</p>

<p>In class we saw bounds for possible errors due the basic floating point property: $fl(x \odot y) = (x \odot y)(1 + \delta)$.</p>

<p>In this XC project, you will compare the theoretical bounds with those you observe with random data.</p>

<p>For example, in Thm 1 on p48 we have a theorem that said adding $n$ <em>positive</em> machine numbers will yield a <em>relative</em> error no more than $n \epsilon$. Here we can see it isn't so severe for the built in sum function, but can be in a loop:</p>

In [1]:
rel_error(a, b) = (a-b)/b
function naive_sum{T}(xs::Vector{T})
  tot = zero(T)
  for x in xs
     tot += x
  end
  tot
end

naive_sum (generic function with 1 method)

In [1]:
n = 1_000_000 # a million
xs = convert.(Float32, rand(n))   # n numbers in (0,1); epsilon ~ 1e-7
xs64 = convert.(Float64, xs)      # smaller epsilon ~ 1e-16
xsbig = convert.(BigFloat, xs)    # much smaller ~ 1e-77

answer = convert(Float64, sum(xsbig))  # basically correct

rel_error(sum(xs),answer),    rel_error(naive_sum(xs), answer),
rel_error(sum(xs64), answer), rel_error(naive_sum(xs64), answer)

(-5.6583953125383846e-8, 2.504820581264218e-6, 0.0, -6.981933265169224e-16)

<p>Compare to</p>

In [1]:
n * eps(Float32), n * eps(Float64)

(0.11920929f0, 2.220446049250313e-10)

<p>The relative errors are well within these worst-case bounds.</p>

<h2>Error in a dot product</h2>

<p>We have this bound: if $x_1, x_2, ...$ and $y_1, y_2, ...$ are machine numbers, then $\sum x_i y_i$ has error bounded by $n \cdot \epsilon$ (cf. p2 of http://www.cs.cornell.edu/~bindel/class/cs6210-f12/notes/lec05.pdf). This was a simplification of Theorem 2 in section 4.9.</p>

<p>Here is the simple dot product (as compared to the <code>dot</code> function):</p>

In [1]:
function naive_dot{T}(xs::Vector{T}, ys::Vector{T})
  tot = zero(T)
  for (x, y) in zip(xs, ys)
    tot = tot + x * y
  end
  tot
end

naive_dot (generic function with 1 method)

<p>This code generates <code>n</code> samples of different types and computes a answer that is reasonably correct:</p>

In [1]:
n = 1_000_000
xs = convert.(Float32, rand(n))
ys = convert.(Float32, rand(n))

xs64 = convert.(Float64, xs)
ys64 = convert.(Float64, ys)

xsbig = convert.(BigFloat, xs)
ysbig = convert.(BigFloat, ys)

answer = convert(Float64, sum(xsbig .* ysbig))

250289.628745621

<p>Finally, this would compute values using the naive defn and one more optimized. </p>

In [1]:
rel_error(dot(xs, ys), answer),
rel_error(naive_dot(xs, ys), answer),
rel_error(dot(xs64, ys64), answer),
rel_error(naive_dot(xs64,  ys64), answer)

(-4.5195888291091337e-7, -0.00014235006779774693, 0.0, 1.1046657854927498e-14)

<p>Run the above in Julia and see if the bounds <code>n * eps</code> are true.</p>

<hr />

<p>Theorem 2 (p249) is more technical than the simplification mentioned in class. It shows that sum computed can be written in terms of $\sum x_i y_i \cdot(1 + \delta_i)$ where each $\delta_i$ is bounded by $6/5(n+1)\epsilon$. Reversing the picture and writing $\tilde{x}_i = x_1 \cdot(1 + \delta_i)$ then</p>


$$
fl(x\cdot y) = \tilde{x} \cdot y.
$$


<p>In mathematics we want to compute $f(x,y)$, but instead, compute $\tilde{f}(x,y) = fl(x \cdot y)$. However, we can view this as $f(\tilde{x}, y)$ where the relative error if $\tilde{x}$ and $x$ are bounded.</p>

<p>Similarly, Theorem 3 (p250) wants to solve $Ax=b$ of $x = f(A, b)$, but instead we get $\tilde{y} =  A \ b$, an approximation. The theorem says this can be written as $\tilde{y} = f(\tilde{A}, b)$ with $\tilde{A} = A + \Delta$ where the values in $\Delta$ are bounded.</p>

<p>These are <em>backwards</em> errors – thinking of errors not as differences amongs the outputs, but as consequences of pertubations of the inputs. If these perturbed inputs are controlled, then the algorithm is considered backwards stable.</p>

<p>Okay, but this is a bit harder to understand. Let's investigate the relative error directly.</p>

<p>How much <em>error</em> comes in computing $Ax = b$? Let's do some experiments:</p>

<p>We begin with a random matrix</p>

In [1]:
n = 10
A = rand(n,n)

10×10 Array{Float64,2}:
 0.780722   0.981938   0.274296    0.50486    0.497084   0.879497  0.435577  0.942401  0.00413468  0.832809 
 0.347788   0.940025   0.836821    0.0364404  0.680633   0.346654  0.475969  0.458393  0.682243    0.388499 
 0.407109   0.344141   0.795184    0.774858   0.871243   0.195755  0.171065  0.793924  0.466979    0.148887 
 0.261394   0.0920519  0.847213    0.765251   0.900517   0.160125  0.609309  0.680125  0.961878    0.461156 
 0.133044   0.453235   0.921808    0.141656   0.0504841  0.442894  0.882444  0.246178  0.00677756  0.287097 
 0.694877   0.536284   0.0325739   0.214301   0.189569   0.527838  0.354677  0.543817  0.554107    0.901118 
 0.865489   0.697072   0.0641422   0.569684   0.435149   0.736459  0.670813  0.612419  0.382979    0.348199 
 0.615644   0.839646   0.331944    0.200916   0.524428   0.308413  0.785978  0.524418  0.695052    0.779913 
 0.0153589  0.495436   0.00502152  0.644476   0.247473   0.12338   0.454633  0.275173  0.26053     0.146

<p>We can create a known answer and vector with:</p>

In [1]:
x = rand(n)
b = A * x
xtilde = A \ b

10-element Array{Float64,1}:
 0.984298 
 0.424604 
 0.0152076
 0.574261 
 0.619192 
 0.913253 
 0.305277 
 0.369715 
 0.838781 
 0.841255 

<p>What is the relative error?</p>

In [1]:
norm(x - xtilde) / norm(x)

1.1442222962538004e-14

<p>Verify that this has small relative error, around $n^2 \epsilon$.</p>

<p>Will this always be true?</p>

<p>The Hilbert matrix has $h_{ij} = 1/(i + j -1)$ and can be created with:</p>

In [1]:
H = [1/(i + j - 1) for i in 1:n, j in 1:n]

10×10 Array{Float64,2}:
 1.0       0.5        0.333333   0.25       0.2        0.166667   0.142857   0.125      0.111111   0.1      
 0.5       0.333333   0.25       0.2        0.166667   0.142857   0.125      0.111111   0.1        0.0909091
 0.333333  0.25       0.2        0.166667   0.142857   0.125      0.111111   0.1        0.0909091  0.0833333
 0.25      0.2        0.166667   0.142857   0.125      0.111111   0.1        0.0909091  0.0833333  0.0769231
 0.2       0.166667   0.142857   0.125      0.111111   0.1        0.0909091  0.0833333  0.0769231  0.0714286
 0.166667  0.142857   0.125      0.111111   0.1        0.0909091  0.0833333  0.0769231  0.0714286  0.0666667
 0.142857  0.125      0.111111   0.1        0.0909091  0.0833333  0.0769231  0.0714286  0.0666667  0.0625   
 0.125     0.111111   0.1        0.0909091  0.0833333  0.0769231  0.0714286  0.0666667  0.0625     0.0588235
 0.111111  0.1        0.0909091  0.0833333  0.0769231  0.0714286  0.0666667  0.0625     0.0588235  0.055

<p>Repeat the above to find the relative error for $H$. Is it like $n^2 \epsilon$? (See p252 if you want a theoretical bound)</p>